In [1]:

%load_ext autoreload
%autoreload 2
import sys
import numpy as np
import pandas as pd
import hydra

from src.ad2s import AD2SDetector
from sklearn.metrics import roc_auc_score
from utils.util import cfg
from utils.synthetic import plot_ds
import time

In [2]:
df = pd.read_csv(cfg.data.save_path)
# You can plot the dataset to see what it looks like
# plot_ds(df)

In [3]:
# Here we initialize the detector
clf = AD2SDetector()

# We collect all the predictions, window sizes and the window reset probability
predict = []
window_size = []
p = []

for data in df['data']:
    score = clf.predict(data)
    predict.append(score)
    window_size.append(clf.window_size)
    p.append(clf.p)


In [4]:
# Cal the AUC score of AD2S for this dataset
df['predict'] = predict
truth = df['label'][df['data']!=0.0]
predict_nonzero = df['predict'][df['data']!=0.0]
auc = roc_auc_score(truth,predict_nonzero)
print(f'AD2S auc score for dataset {cfg.data.synthetic_ds}: {auc:10.3f}')

AD2S auc score for dataset 1:      0.980


In [5]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
fig = make_subplots(rows=4,cols=1,shared_xaxes=True)
fig.add_trace(
    go.Scatter(
    x=df.index,
    y = df['data'],
    mode="lines+markers",
    selectedpoints = np.where(df['label']==True)[0],
    selected=dict(marker=dict(color="red", size=4)),
    unselected=dict(marker=dict(size=0)),
    name='Observations'
    ),
    row=1,col=1
)
fig.add_trace(go.Scatter(y=predict,mode="lines",name='Scores'),row=2,col=1)
fig.add_trace(go.Scatter(y=window_size,mode="lines",name='Window size'),row=3,col=1)
fig.add_trace(go.Scatter(y=p,mode="lines",name='Window reset probability'),row=4,col=1)